### Why Create a Use Case? 

Creating a Use Case in FeatureByte, while optional, offers significant benefits. It not only defines the goal and application of your prediction model but also helps organize your training data and improve post-deployment feature monitoring. 

Plus, for FeatureByte Enterprise users, it's used by FeatureByte Copilot to suggest features tailored to your use cases.

We'll create one Use Case for our Grocery Dataset: **In-Store Prediction of Customer Spending on a given Product Group next 2 Weeks**.

We will first establish a Target, define a Context and then link the Use Case with the Context and Target.

In [1]:
import featurebyte as fb

# Set your profile to the tutorial environment
fb.use_profile("tutorial")

catalog_name = "Grocery Dataset Tutorial"
catalog = fb.Catalog.activate(catalog_name)  

15:28:55 | INFO     | SDK version: 1.0.2.dev46


15:28:55 | INFO     | No catalog activated.


15:28:55 | INFO     | Using profile: tutorial


15:28:56 | INFO     | Using configuration file at: /Users/gxav/.featurebyte/config.yaml


15:28:56 | INFO     | Active profile: tutorial (https://tutorials.featurebyte.com/api/v1)


15:28:56 | INFO     | SDK version: 1.0.2.dev46


15:28:56 | INFO     | No catalog activated.


15:28:56 | INFO     | Catalog activated: Grocery Dataset Tutorial


#### Creating a Target

We will work with INVOICEITEMS which is the table indicating the details of each invoice. For convenience, "GroceryCustomerGuid", representing the customer entity, is already added to the view of INVOICEITEMS. We will also join "GROCERYPRODUCT" to populate the "ProductGroup" column representing the productgroup entity.

In [2]:
# Get view from GROCERYPRODUCT dimension table.
groceryproduct_view = catalog.get_view("GROCERYPRODUCT")
# Get view from INVOICEITEMS item table.
invoiceitems_view = catalog.get_view("INVOICEITEMS")
# Join GROCERYPRODUCT view to INVOICEITEMS view.
invoiceitems_view = invoiceitems_view.join(groceryproduct_view, rsuffix="")

The target is a sum of the TotalCost column in next 14d per customer (GroceryCustomerGuid) and productgroup (ProductGroup).

In [3]:
target = invoiceitems_view\
    .groupby(['GroceryCustomerGuid', 'ProductGroup'])\
    .forward_aggregate(
        "TotalCost", method="sum",
        target_name="CUSTOMER_x_PRODUCTGROUP_Sum_of_TotalCost_next_2_weeks",
        window='14d',
        fill_value=0
    )

In order for a target (or a feature) to be recorded in catalog, we need to save it:

In [4]:
target.save()

Also we will update description of the target.

In [5]:
target.update_description(
    "Sum of Total spent by the customer for a given product group over the next 14d period."
)

Target is created. We can check target's definition file, which provides explicit outline of all operations for declaration of the target.
For example this definition includes implicit operations like all cleaning operations inherited from the table. 

In [6]:
target.definition

'# Generated by SDK version: 1.0.2.dev46\nfrom bson import ObjectId\nfrom featurebyte import DimensionTable\nfrom featurebyte import ItemTable\n\n\n# item_table name: "INVOICEITEMS", event_table name: "GROCERYINVOICE"\nitem_table = ItemTable.get_by_id(ObjectId("662b5778aa13c89fa14554e2"))\nitem_view = item_table.get_view(\n    event_suffix=None,\n    view_mode="manual",\n    drop_column_names=["record_available_at"],\n    column_cleaning_operations=[],\n    event_drop_column_names=["record_available_at"],\n    event_column_cleaning_operations=[],\n    event_join_column_names=[\n        "Timestamp",\n        "GroceryInvoiceGuid",\n        "GroceryCustomerGuid",\n        "tz_offset",\n    ],\n)\n\n# dimension_table name: "GROCERYPRODUCT"\ndimension_table = DimensionTable.get_by_id(ObjectId("662b577aaa13c89fa14554e3"))\ndimension_view = dimension_table.get_view(\n    view_mode="manual", drop_column_names=[], column_cleaning_operations=[]\n)\njoined_view = item_view.join(\n    dimension_view, on="GroceryProductGuid", how="left", rsuffix="", rprefix=""\n)\ntarget = joined_view.groupby(\n    by_keys=["GroceryCustomerGuid", "ProductGroup"], category=None\n).forward_aggregate(\n    value_column="TotalCost",\n    method="sum",\n    window="14d",\n    target_name="CUSTOMER_x_PRODUCTGROUP_Sum_of_TotalCost_next_2_weeks",\n    skip_fill_na=True,\n)\ntarget_1 = target.copy()\ntarget_1[target.isnull()] = 0\ntarget_1.name = "CUSTOMER_x_PRODUCTGROUP_Sum_of_TotalCost_next_2_weeks"\noutput = target_1\noutput.save(_id=ObjectId("662b57ba7b0ec8565570b78c"))\n'

#### Creating a Context

A Context defines the scope and circumstances in which features are expected to be served.

Let's describe the Context for our use case:

- **Context Name**: In-Store Customer Engagement with ProductGroup
- **Primary Entity**: customer, productgroup
- **Description**: Evaluate future customer engagement with ProductGroup during its visit in the store to improve its shopping experience.


In [7]:
fb.Context.create(
    name="In-Store Customer Engagement with ProductGroup",
    primary_entity=["customer", "productgroup"],
    description="Evaluate future customer engagement with ProductGroup during its visit in the store to improve its shopping experience."
)

<featurebyte.api.context.Context at 0x156ed7040>
{
  'name': 'In-Store Customer Engagement with ProductGroup',
  'created_at': '2024-04-26T07:29:00.642000',
  'updated_at': None,
  'description': 'Evaluate future customer engagement with ProductGroup during its visit in the store to improve its shopping experience.',
  'author': None,
  'primary_entities': [
    {
      'name': 'productgroup',
      'serving_names': [
        'PRODUCTGROUP'
      ],
      'catalog_name': 'Grocery Dataset Tutorial'
    },
    {
      'name': 'customer',
      'serving_names': [
        'GROCERYCUSTOMERGUID'
      ],
      'catalog_name': 'Grocery Dataset Tutorial'
    }
  ],
  'default_eda_table': None,
  'default_preview_table': None,
  'associated_use_cases': []
}

#### Creating a Use Case

Let's link our Use Case with the Context and Target.

In [8]:
fb.UseCase.create(
    name="In-Store Prediction of Customer Spending on a given Product Group next 2 Weeks",
    context_name="In-Store Customer Engagement with ProductGroup",
    target_name="CUSTOMER_x_PRODUCTGROUP_Sum_of_TotalCost_next_2_weeks",
    description="Predict the expenditure of customer on a specific product group within a two-week period starting from the time of its visit in the store. This use case will help improve customer shopping experience."
)

<featurebyte.api.use_case.UseCase at 0x156f63cd0>
{
  'name': 'In-Store Prediction of Customer Spending on a given Product Group next 2 Weeks',
  'created_at': '2024-04-26T07:29:02.229000',
  'updated_at': None,
  'description': 'Predict the expenditure of customer on a specific product group within a two-week period starting from the time of its visit in the store. This use case will help improve customer shopping experience.',
  'author': None,
  'primary_entities': [
    {
      'name': 'productgroup',
      'serving_names': [
        'PRODUCTGROUP'
      ],
      'catalog_name': 'Grocery Dataset Tutorial'
    },
    {
      'name': 'customer',
      'serving_names': [
        'GROCERYCUSTOMERGUID'
      ],
      'catalog_name': 'Grocery Dataset Tutorial'
    }
  ],
  'context_name': 'In-Store Customer Engagement with ProductGroup',
  'target_name': 'CUSTOMER_x_PRODUCTGROUP_Sum_of_TotalCost_next_2_weeks',
  'default_eda_table': None,
  'default_preview_table': None
}

#### Listing targets, contexts and use cases in the catalog

In [9]:
catalog.list_targets()

id  \
0  662b57ba7b0ec8565570b78c   

                                                name  dtype  \
0  CUSTOMER_x_PRODUCTGROUP_Sum_of_TotalCost_next_...  FLOAT   

                   entities                  created_at  
0  [customer, productgroup]  2024-04-26T07:28:59.403000

In [10]:
catalog.list_contexts()

id                                            name  \
0  662b57bc7b0ec8565570b78e  In-Store Customer Engagement with ProductGroup   

                                  primary_entity_ids  \
0  [662b578e228ac8cf5c5c926a, 662b5791228ac8cf5c5...   

                                         description  
0  Evaluate future customer engagement with Produ...

In [11]:
catalog.list_use_cases()

id  \
0  662b57bd7b0ec8565570b790   

                                                name  \
0  In-Store Prediction of Customer Spending on a ...   

  default_preview_table_name default_eda_table_name  \
0                         []                     []   

                                         description  
0  Predict the expenditure of customer on a speci...

### Concepts discussed in this tutorial 
- [More about feature definition file](https://docs.featurebyte.com/latest/about/glossary/#feature-definition-file)

#### SDK reference for
- [Target](https://docs.featurebyte.com/latest/reference/core/target/)
- [Context](https://docs.featurebyte.com/latest/reference/core/context/)
- [Use Case](https://docs.featurebyte.com/latest/reference/core/use_case/)
- [View.groupby()](https://docs.featurebyte.com/latest/reference/featurebyte.api.view.GroupByMixin.groupby/)
- [GroupBy.forward_aggregate()](https://docs.featurebyte.com/latest/reference/featurebyte.api.groupby.GroupBy.forward_aggregate/)
- [Aggregation functions](https://docs.featurebyte.com/latest/reference/featurebyte.enum.AggFunc/)
- [Target.definition](https://docs.featurebyte.com/latest/reference/featurebyte.api.target.Target.definition/)
